In [1]:
import numpy as np
import astropy
from itertools import izip
from os.path import join
from pearce.mocks import compute_prim_haloprop_bins, cat_dict
from pearce.mocks.customHODModels import *
from halotools.sim_manager import TabularAsciiReader
from halotools.utils.table_utils import compute_conditional_percentiles
from halotools.mock_observables import hod_from_mock, wp, tpcf, tpcf_one_two_halo_decomp
from halotools.custom_exceptions import HalotoolsError
from math import ceil

In [2]:
from matplotlib import pyplot as plt
%matplotlib inline
import seaborn as sns
sns.set()

In [3]:
boxno = 0
a = 0.645161 # ~ z = 0.5
cosmo_params = {'simname':'testbox', 'boxno':boxno,'realization':0, 'scale_factors':[a]}
cat = cat_dict[cosmo_params['simname']](**cosmo_params)#construct the specified catalog!

cat.load_catalog(a)

In [4]:
ab = False
hodname = 'hsabRedMagic' if ab else 'redMagic'

In [5]:
cat.load_model(a, hodname, hod_kwargs= {'prim_haloprop_key':'halo_m200b',
                                             'halo_mass_column_key': 'halo_m200b'})

In [6]:
cat.model.param_dict

{'alpha': 1.02,
 'f_c': 0.19,
 'logM0': 12.2,
 'logM1': 13.7,
 'logMmin': 12.1,
 'sigma_logM': 0.46}

Params taken from Beth Reid et al 2014.

In [7]:
params = {'logMmin':13.031,
          'sigma_logM':0.38,
          'logM0':13.27,
          'logM1':14.08,
          'alpha':0.76,
          'f_c': 1.0
            }

AB params chosen as sensible guesses of my own choosing. Should approximate a SHAM, but not exactly. 

In [8]:
params['mean_occupation_centrals_assembias_param1'] = 0.7
params['mean_occupation_satellites_assembias_param1'] = -0.5 

These catalogs only have m200, not mvir. Turns out halotools does not handle switching between the two more difficult than anticipated. I'm going to do something sinful: make a halo_mvir column that is actually the m200b column. I have to delete it before I save the catalog though. 

In [9]:
#magic, don't delete
try:
    cat.halocat.halo_table['halo_mvir']
except HalotoolsError:
    try:
        cat.halocat.halo_table['halo_mvir']
    except KeyError:
        pass

There is an issue with the outbgc2 catalogs. They don't have `rs`'s, but the out catalogs do. I'll have to think of somethign cleaner for using these boxes later in the future (or just rerun bgc2) but for now i'll manually add the column to the table. 

In [10]:
1.0/(1.0+cat.halocat.redshift)

0.6451612903225806

In [11]:
cat.filenames

['/u/ki/swmclau2/des/testbox_findparents/TestBox000-000_out_parents_5.list']

In [12]:
cat.halocat.halo_table['halo_mvir'] = cat.halocat.halo_table['halo_m200b']
cat.halocat.halo_table['halo_rvir'] = cat.halocat.halo_table['halo_r200b']
cat.halocat.halo_table['halo_r200b_conc'] = cat.halocat.halo_table['halo_r200b']/cat.halocat.halo_table['halo_rs']
cat.halocat.halo_table['halo_nfw_conc'] = cat.halocat.halo_table['halo_r200b_conc']

In [13]:
cat.populate(params)

In [14]:
galcat = cat.model.mock.galaxy_table

In [15]:
del galcat['halo_mvir']
del galcat['halo_rvir']
#del galcat['conc_NFWmodel']
del galcat['gal_type']

In [16]:
%%bash
pwd
h5ls cmass_hod_catalog.hdf5

/nfs/slac/g/ki/ki18/des/swmclau2/AB_tests
box0_ab_False            Dataset {403172}
box0_ab_True             Dataset {402645}
box1_ab_False            Dataset {402283}
box1_ab_True             Dataset {402875}
box2_ab_False            Dataset {402885}
box2_ab_True             Dataset {401997}


In [28]:
np.sum(galcat['host_centric_distance'] > 0)

45705

In [29]:
len(galcat)

402485

In [1]:
%%bash 
ls /u/ki/swmclau2/des/*

/u/ki/swmclau2/des/2LPTic.tar.gz
/u/ki/swmclau2/des/DR10_cBOSS_WISE_SMF_z0.45_0.60_M7.dat
/u/ki/swmclau2/des/Multidark SHAM.ipynb
/u/ki/swmclau2/des/Nov2016.tar.gz
/u/ki/swmclau2/des/SHAMs4Jeremey+Zhongxu.ipynb
/u/ki/swmclau2/des/catalog_ab_halo_mpeak.csv
/u/ki/swmclau2/des/catalog_ab_halo_mpeak_fixed.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_mpeak_fixed_large.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_mpeak_shuffled_fixed.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak.csv
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak_2.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak_fixed.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak_fixed_large.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak_shuffled.hdf5
/u/ki/swmclau2/des/catalog_ab_halo_vmax@mpeak_shuffled_fixed.hdf5
/u/ki/swmclau2/des/catalog_gama_downsampled_mag_16.hdf5
/u/ki/swmclau2/des/emulator_tarfile.zip
/u/ki/swmclau2/des/galaxyzoo-master.zip
/u/ki/swmclau2/des/md_catalog_ab_halo